In [3]:
import numpy as np
import pandas as pd
import keras
import tensorflow
import matplotlib.pyplot as plt

from csv import writer
from sklearn.ensemble import RandomForestRegressor
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Dense, Input, BatchNormalization
from tensorflow.keras import optimizers
from tensorflow.keras.optimizers import Adam
from sklearn.metrics import explained_variance_score
from sklearn.preprocessing import Normalizer
from sklearn import metrics
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error


def autoencoder(dfx, y, dims, component):

    regr = LinearRegression()
    variance_list = []
    r2_list = []
    for i in range(1, dims):
        print('---------- Autoencoder dim {} ----------'.format(i))
        # Training and test splits
        train, dev, train_labels, dev_labels = train_test_split(dfx, y, test_size=0.20, random_state=40)
        train, test, train_labels, test_labels = train_test_split(train, train_labels, test_size=0.20, random_state=40)
        input_data = Input(shape=(1537,))

        x_train = train.loc[:, train.columns]
        x_test = test.loc[:, test.columns]
        x_dev = dev.loc[:, dev.columns]

        encoded = Dense(i, activation='tanh', name='bottleneck')(input_data)
        decoded = Dense(1537, activation='tanh')(encoded)

        autoencoder = Model(input_data, decoded)

        # Compile the autoencoder
        autoencoder.compile(loss='mean_squared_error', optimizer=Adam(learning_rate=0.0001))
        autoencoder.summary()

        trained_model = autoencoder.fit(
            x_train, 
            x_train, 
            batch_size=128, 
            epochs=50, 
            verbose=1,
            validation_data=(x_dev, x_dev)
        )

        # Bottleneck representation
        encoder = Model(autoencoder.input, autoencoder.get_layer('bottleneck').output)
        encoded_data = encoder.predict(x_train)  
        decoded_output = autoencoder.predict(x_train)  
        decoded_output_test = autoencoder.predict(x_test)

        # Variance score explanation
        regr.fit(encoded_data, train_labels)

        encoded_data_test = encoder.predict(x_test)
        y_pred = regr.predict(encoded_data_test) # << Pass x_test to get predicitons for original uncompressed
        
        # Variance and r2 scores for the regression model
        variance = regr.score(encoded_data_test, test_labels) # << pass in x test for uncompressed values
        r2_val = r2_score(test_labels, y_pred)
        print ('Variance score: %.2f' % variance)
        print ('R Square', r2_val)

        # Add r2/variance to lists
        variance_list.append(variance)
        r2_list.append(r2_val)        

    # Write entry to file
    file_name = 'C:\\Users\\Kurly\\Downloads\\Universal-Embeddings-testing\\Universal-Embeddings-Nick\\data\\{}_ae_test.csv'.format(component)
    write_data = pd.DataFrame(data={'{}_var'.format(component): variance_list, '{}_r2'.format(component): r2_list})
    write_data.to_csv(path_or_buf=file_name, index=False)

    return (variance_list, r2_list)


def ae_linegraph(num_of_comp, component_names, colors_list):
    ''' 
    Plot a linegraph for pca
    '''
    
    plt.figure(figsize=(12,10))
    plt.rcParams.update({'font.size': 18})
    for i, component in enumerate(component_names):
        print('--- Autoencoder for {} ---'.format(component))
        # Open model folder
        file_name = 'C:\\Users\\Kurly\\Downloads\\Universal-Embeddings-testing\\Universal-Embeddings-Nick\\data\\{}_ae_test.csv'.format(component)
        model = pd.read_csv(filepath_or_buffer=file_name)
        #print(model['{}_var'.format(component)])
        #print(model['{}_r2'.format(component)])

        variance = model['{}_var'.format(component)]
        r2 = model['{}_r2'.format(component)]
        
        #variance, r2 = autoencoder(dfx, y, dims, component)
        plt.plot(num_of_comp, variance[:11], label = '{}'.format(component), linestyle = '-', marker = '+', color = colors_list[i])
        plt.plot(num_of_comp, r2[:11], linestyle = '-.', marker = 'H', color = colors_list[i])
        plt.xlabel('Dimension')
        plt.ylabel('Variance/R2')
        plt.title('Autoencoder of Polluting Gases')
        plt.legend()
    plt.show()

### RUN ###

# COMPONENT_NAMES = ['co', 'no', 'no2', 'o3', 'so2', 'pm2_5', 'pm10', 'nh3']
COMPONENT_NAMES = ['all']
COLORS_LIST = ['tab:blue', 'tab:green', 'tab:orange', 'tab:red', 'tab:purple', 'tab:cyan', 'tab:olive', 'tab:pink']
# Starting dimensions
DIMS = 1536
# Number of components
#NUM_OF_COMP=list(range(2,191))
NUM_OF_COMP=list(range(2,1537))

#ae_linegraph(NUM_OF_COMP, COMPONENT_NAMES, COLORS_LIST)

for i, component in enumerate(COMPONENT_NAMES):

    df = pd.read_csv('C:\\Users\\Kurly\\Downloads\\Universal-Embeddings-testing\\Universal-Embeddings-Nick\\data\\all_data_clean.csv'.format(component))
    columns = list(df.columns.values)

    # Features list and removal of city, lat, lon
    features = list(df.columns.values)
    del features[:1]
    del features[-1]

    # y value list using last day of 7-month data
    y = df.loc[:, ['nh3_2021_06_06'.format(component)]].values

    # Normalize x values; save in data frame
    x = df.loc[:, features].values
    x = Normalizer().fit_transform(x)
    dfx = pd.DataFrame(x)

    print('--- Autoencoder for {} ---'.format(component))
    variance, r2 = autoencoder(dfx, y, DIMS, component)


--- Autoencoder for all ---
---------- Autoencoder dim 1 ----------
Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_3 (InputLayer)         [(None, 1537)]            0         
_________________________________________________________________
bottleneck (Dense)           (None, 1)                 1538      
_________________________________________________________________
dense_1 (Dense)              (None, 1537)              3074      
Total params: 4,612
Trainable params: 4,612
Non-trainable params: 0
_________________________________________________________________
Epoch 1/50
93/93 [==============================] - 1s 6ms/step - loss: 5.5737e-04 - val_loss: 4.6659e-04
Epoch 2/50
93/93 [==============================] - 0s 4ms/step - loss: 3.8043e-04 - val_loss: 2.9119e-04
Epoch 3/50
93/93 [==============================] - 0s 3ms/step - loss: 2.1422e-04 - val_loss: 1.4549e-04
E

Epoch 31/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8093e-05 - val_loss: 1.7765e-05
Epoch 32/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8081e-05 - val_loss: 1.7749e-05
Epoch 33/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8067e-05 - val_loss: 1.7732e-05
Epoch 34/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8053e-05 - val_loss: 1.7721e-05
Epoch 35/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8037e-05 - val_loss: 1.7707e-05
Epoch 36/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8021e-05 - val_loss: 1.7687e-05
Epoch 37/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8004e-05 - val_loss: 1.7672e-05
Epoch 38/50
93/93 [==============================] - 0s 4ms/step - loss: 1.7985e-05 - val_loss: 1.7653e-05
Epoch 39/50
93/93 [==============================] - 0s 4ms/step - loss: 1.7963e-05 - val_loss: 1.7634e-05
Epoch 40/50
93/93 [==================

Epoch 50/50
93/93 [==============================] - 0s 4ms/step - loss: 1.7019e-05 - val_loss: 1.6692e-05
Variance score: 0.08
R Square 0.08408404602300912
---------- Autoencoder dim 5 ----------
Model: "model_9"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_7 (InputLayer)         [(None, 1537)]            0         
_________________________________________________________________
bottleneck (Dense)           (None, 5)                 7690      
_________________________________________________________________
dense_5 (Dense)              (None, 1537)              9222      
Total params: 16,912
Trainable params: 16,912
Non-trainable params: 0
_________________________________________________________________
Epoch 1/50
93/93 [==============================] - 1s 6ms/step - loss: 5.4331e-04 - val_loss: 4.1867e-04
Epoch 2/50
93/93 [==============================] - 0s 4ms/step - loss: 2.7744e-04

93/93 [==============================] - 0s 4ms/step - loss: 1.8266e-05 - val_loss: 1.7919e-05
Epoch 12/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8242e-05 - val_loss: 1.7899e-05
Epoch 13/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8223e-05 - val_loss: 1.7880e-05
Epoch 14/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8204e-05 - val_loss: 1.7866e-05
Epoch 15/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8188e-05 - val_loss: 1.7851e-05
Epoch 16/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8172e-05 - val_loss: 1.7835e-05
Epoch 17/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8157e-05 - val_loss: 1.7824e-05
Epoch 18/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8144e-05 - val_loss: 1.7811e-05
Epoch 19/50
93/93 [==============================] - 0s 4ms/step - loss: 1.8131e-05 - val_loss: 1.7797e-05
Epoch 20/50
93/93 [==============================

Epoch 48/50
93/93 [==============================] - 0s 4ms/step - loss: 1.5481e-05 - val_loss: 1.5173e-05
Epoch 49/50
93/93 [==============================] - 0s 4ms/step - loss: 1.5332e-05 - val_loss: 1.5032e-05
Epoch 50/50
93/93 [==============================] - 0s 4ms/step - loss: 1.5200e-05 - val_loss: 1.4900e-05
Variance score: 0.07
R Square 0.06646999327195724
---------- Autoencoder dim 9 ----------
Model: "model_17"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_11 (InputLayer)        [(None, 1537)]            0         
_________________________________________________________________
bottleneck (Dense)           (None, 9)                 13842     
_________________________________________________________________
dense_9 (Dense)              (None, 1537)              15370     
Total params: 29,212
Trainable params: 29,212
Non-trainable params: 0
_______________________________________

...

93/93 [==============================] - 3s 37ms/step - loss: 6.0017e-06 - val_loss: 5.9959e-06
Epoch 38/50
93/93 [==============================] - 3s 37ms/step - loss: 5.8828e-06 - val_loss: 5.8821e-06
Epoch 39/50
93/93 [==============================] - 3s 37ms/step - loss: 5.7684e-06 - val_loss: 5.7645e-06
Epoch 40/50
93/93 [==============================] - 4s 39ms/step - loss: 5.6583e-06 - val_loss: 5.6566e-06
Epoch 41/50
93/93 [==============================] - 4s 39ms/step - loss: 5.5545e-06 - val_loss: 5.5569e-06
Epoch 42/50
93/93 [==============================] - 3s 37ms/step - loss: 5.4532e-06 - val_loss: 5.4585e-06
Epoch 43/50
93/93 [==============================] - 3s 37ms/step - loss: 5.3564e-06 - val_loss: 5.3668e-06
Epoch 44/50
93/93 [==============================] - 3s 38ms/step - loss: 5.2624e-06 - val_loss: 5.2761e-06
Epoch 45/50
93/93 [==============================] - 4s 39ms/step - loss: 5.1735e-06 - val_loss: 5.1851e-06
Epoch 46/50
93/93 [=====================

Epoch 1/50
93/93 [==============================] - 4s 40ms/step - loss: 1.5680e-04 - val_loss: 3.2217e-05
Epoch 2/50
93/93 [==============================] - 4s 38ms/step - loss: 3.0577e-05 - val_loss: 2.8106e-05
Epoch 3/50
93/93 [==============================] - 3s 38ms/step - loss: 2.6762e-05 - val_loss: 2.4821e-05
Epoch 4/50
93/93 [==============================] - 3s 38ms/step - loss: 2.3758e-05 - val_loss: 2.2262e-05
Epoch 5/50
93/93 [==============================] - 4s 38ms/step - loss: 2.1348e-05 - val_loss: 2.0116e-05
Epoch 6/50
93/93 [==============================] - 3s 37ms/step - loss: 1.9390e-05 - val_loss: 1.8397e-05
Epoch 7/50
93/93 [==============================] - 3s 37ms/step - loss: 1.7793e-05 - val_loss: 1.7021e-05
Epoch 8/50
93/93 [==============================] - 3s 37ms/step - loss: 1.6481e-05 - val_loss: 1.5824e-05
Epoch 9/50
93/93 [==============================] - 4s 39ms/step - loss: 1.5381e-05 - val_loss: 1.4828e-05
Epoch 10/50
93/93 [==================

93/93 [==============================] - 3s 36ms/step - loss: 5.9896e-06 - val_loss: 5.9993e-06
Epoch 38/50
93/93 [==============================] - 3s 35ms/step - loss: 5.8706e-06 - val_loss: 5.8893e-06
Epoch 39/50
93/93 [==============================] - 3s 35ms/step - loss: 5.7566e-06 - val_loss: 5.7676e-06
Epoch 40/50
93/93 [==============================] - 3s 35ms/step - loss: 5.6470e-06 - val_loss: 5.6646e-06
Epoch 41/50
93/93 [==============================] - 3s 36ms/step - loss: 5.5433e-06 - val_loss: 5.5663e-06
Epoch 42/50
93/93 [==============================] - 3s 35ms/step - loss: 5.4407e-06 - val_loss: 5.4617e-06
Epoch 43/50
93/93 [==============================] - 3s 35ms/step - loss: 5.3436e-06 - val_loss: 5.3677e-06
Epoch 44/50
93/93 [==============================] - 3s 34ms/step - loss: 5.2506e-06 - val_loss: 5.2761e-06
Epoch 45/50
93/93 [==============================] - 3s 35ms/step - loss: 5.1631e-06 - val_loss: 5.1906e-06
Epoch 46/50
93/93 [=====================

Epoch 1/50
93/93 [==============================] - 4s 39ms/step - loss: 1.5053e-04 - val_loss: 3.1952e-05
Epoch 2/50
93/93 [==============================] - 3s 37ms/step - loss: 3.0366e-05 - val_loss: 2.7837e-05
Epoch 3/50
93/93 [==============================] - 3s 37ms/step - loss: 2.6552e-05 - val_loss: 2.4599e-05
Epoch 4/50
93/93 [==============================] - 3s 37ms/step - loss: 2.3562e-05 - val_loss: 2.2036e-05
Epoch 5/50
93/93 [==============================] - 3s 36ms/step - loss: 2.1174e-05 - val_loss: 1.9922e-05
Epoch 6/50
93/93 [==============================] - 3s 38ms/step - loss: 1.9244e-05 - val_loss: 1.8252e-05
Epoch 7/50
93/93 [==============================] - 4s 38ms/step - loss: 1.7675e-05 - val_loss: 1.6841e-05
Epoch 8/50
93/93 [==============================] - 3s 36ms/step - loss: 1.6371e-05 - val_loss: 1.5678e-05
Epoch 9/50
93/93 [==============================] - 3s 35ms/step - loss: 1.5288e-05 - val_loss: 1.4704e-05
Epoch 10/50
93/93 [==================

KeyboardInterrupt: 